# **Importar Librerias Necesarias**

In [0]:
%pip install emoji
%pip install wordcloud
%pip install matplotlib
%pip install tensorflow

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
import re
import emoji
import builtins

import pandas as pd
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from wordcloud import WordCloud

from pyspark.sql import Row
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from pyspark.sql import functions as F
from pyspark.sql.window import Window
from IPython.display import display, HTML

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from pyspark.sql.types import StringType, IntegerType, NumericType, ArrayType, MapType
from pyspark.ml.feature import Tokenizer, StopWordsRemover, RegexTokenizer

# **Crear Sesión Spark**

In [0]:
spark = SparkSession.builder \
    .appName("EDA_Suicide_Watch") \
    .getOrCreate()

# **Cargar Tabla Registrada Unity Catalog**

Aqui se realizará la carga del conjunto de datos directamente desde la tabla registrada en el entorno de trabajo de Spark. Una vez importada, se muestra su contenido para verificar que la lectura se haya realizado correctamente y para obtener una primera vista general de las filas y columnas disponibles.

In [0]:
df = spark.table("workspace.suicide_detection.suicide_detection_raw")
display(df)

DataFrame[id: bigint, text: string, class: string]

---


---
#<center> **Pre-Procesamiento Conjunto Datos**</center>
---


---


En esta sección se llevará a cabo la preparación inicial del conjunto de datos con el fin de garantizar que la información se encuentre organizada, depurada y lista para ser transformada. Se aplicarán procedimientos orientados a estructurar el conjunto de datos, revisar la calidad de los registros y establecer las bases necesarias para iniciar la limpieza y normalización del texto.

Estos pasos permitirán disponer de un dataset coherente y manejable, asegurando que las etapas posteriores de procesamiento se ejecuten sobre datos consistentes y adecuadamente preparados.

##**Normalización & Limpieza Básica Texto**

En esta sección se llevará a cabo el proceso fundamental de depuración y estandarización del texto, aplicando una serie de transformaciones que permitirán obtener una representación más clara y uniforme del contenido. Estas operaciones estarán enfocadas en eliminar variaciones superficiales, reducir ruido lingüístico y asegurar que cada registro cuente con un formato coherente.

Con estas acciones, se establecerá la base necesaria para que los pasos posteriores puedan trabajar sobre texto limpio y homogéneo, facilitando el análisis y mejorando la calidad del procesamiento subsiguiente.

###**Conversión Texto Minúsculas**

En este apartado se llevará a cabo una visualización comparativa que permitirá observar cómo se verá el texto antes y después de aplicar la conversión a minúsculas. Para ello, se seleccionará una muestra de registros y se generarán dos columnas: una con el texto original y otra con su versión transformada. Esta comparación facilitará verificar que la normalización se esté realizando correctamente antes de aplicarla al resto del conjunto de datos.

Posteriormente, una vez validado el resultado, se aplicará la transformación al dataframe completo, garantizando que todos los registros cuenten con una representación textual unificada en minúsculas.

In [0]:
# Muestra antes/después
df_preview = df.select("id", F.col("text").alias("before")).limit(10)
df_preview = df_preview.withColumn("after", F.lower(F.col("before")))

# Visualizar el Antes vs Después (lowercase)
display(df_preview.toPandas())

# Aplicar transformación al dataframe original
df = df.withColumn("text", F.lower(F.col("text")))

id  ...                                              after
0   2  ...  ex wife threatening suiciderecently i left my ...
1   3  ...  am i weird i don't get affected by compliments...
2   4  ...  finally 2020 is almost over... so i can never ...
3   8  ...          i need helpjust help me im crying so hard
4   9  ...  i’m so losthello, my name is adam (16) and i’v...
5  11  ...  honetly idki dont know what im even doing here...
6  12  ...  [trigger warning] excuse for self inflicted bu...
7  13  ...   it ends tonight.i can’t do it anymore. \ni quit.
8  16  ...  everyone wants to be "edgy" and it's making me...
9  18  ...  my life is over at 20 years oldhello all. i am...

[10 rows x 3 columns]

###**Eliminación Emojis & Caracteres Unicode Especiales**

En este apartado se llevará a cabo la creación de una función personalizada que permitirá remover emojis del texto, sustituyéndolos por una cadena vacía. Para validar su correcto funcionamiento, primero se seleccionará una muestra aleatoria de registros que contengan caracteres fuera del rango ASCII, ya que estos suelen incluir emojis u otros símbolos especiales.

A partir de esta muestra, se generará una vista comparativa con las columnas “before” y “after”, lo que permitirá observar directamente cuáles textos experimentarán cambios tras la limpieza. Luego, se filtrarán únicamente aquellos casos donde la transformación haya producido diferencias, y se mostrará una tabla desplazable que facilitará revisar el resultado de forma ordenada.

Una vez verificada la efectividad del procedimiento, se aplicará la función de eliminación de emojis a todo el dataframe, garantizando que el conjunto completo de textos quede libre de estos caracteres.

In [0]:
# Función para remover emojis
def remove_emoji(text):
    if text is None:
        return text
    return emoji.replace_emoji(text, replace='')

remove_emoji_udf = F.udf(remove_emoji, StringType())

# Crear preview de textos con emojis
df_emoji_preview = (
    df
    .filter(F.col("text").rlike("[^\x00-\x7F]"))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(200)
)

# Crear preview Antes/Despues
df_emoji_preview = df_emoji_preview.withColumn(
    "after",
    remove_emoji_udf(F.col("before"))
)

# Filtrar solo los registros donde sí hubo cambio
df_emoji_changed = df_emoji_preview.filter(F.col("before") != F.col("after")).limit(10)

# Convertir a pandas
preview_pd = df_emoji_changed.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll

display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: nowrap;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn("text", remove_emoji_udf(F.col("text")))

###**Remover Caracteres Control**

En este apartado se llevará a cabo la identificación y limpieza de caracteres de control presentes en el texto, los cuales pertenecen a rangos Unicode que no representan contenido legible y que pueden interferir con los procesos posteriores. Para ello, se filtrará una muestra de registros que contengan este tipo de caracteres y se generará una vista comparativa que mostrará el texto antes y después de la transformación.

La visualización permitirá verificar que dichos caracteres serán reemplazados por espacios en blanco, evitando así distorsiones o rupturas en el contenido. Una vez validado el resultado en la muestra, se aplicará la misma expresión regular al dataframe completo, asegurando que todos los registros queden libres de estos símbolos no imprimibles.

In [0]:
# Filtrar solo textos que contienen caracteres Unicode a limpiar
df_preview = (
    df
    .filter(F.col("text").rlike(r"[\u0000-\u001F\u007F]"))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(10)
)

# Aplicar la normalización solo para visualización
df_preview = df_preview.withColumn(
    "after",
    F.regexp_replace("before", r"[\u0000-\u001F\u007F]", " ")
)

# Convertir a pandas
preview_pd = df_preview.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: nowrap;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    F.regexp_replace("text", r"[\u0000-\u001F\u007F]", " ")
)

###**Normalización Espacios Múltiples**

En este apartado se llevará a cabo una revisión del texto para identificar aquellos casos donde aparezcan espacios repetidos o distribuidos de manera irregular. Para facilitar esta revisión, primero se tomará una muestra del dataset y se mostrará una comparación entre el texto original y la versión corregida, lo que permitirá confirmar que los cambios se están aplicando correctamente.

Una vez validada la transformación, el proceso se aplicará al conjunto completo de datos, reemplazando los espacios múltiples por un único espacio y ajustando la estructura final del texto. Además, se realizará un conteo que permitirá conocer cuántos registros presentaban este tipo de inconsistencias. Con ello, se garantizará que el texto quede más ordenado y uniforme antes de avanzar a las siguientes etapas de procesamiento.

In [0]:
# Tomar una muestra grande para encontrar cambios
df_sample = (
    df
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(200)
)

# Aplicar el proceso a la muestra
df_sample = (
    df_sample
    .withColumn("after_temp", F.regexp_replace("before", r"\s{2,}", " "))
    .withColumn("after", F.trim(F.col("after_temp")))
    .drop("after_temp")
)

# Filtrar solo donde hubo cambios reales
df_changed = df_sample.filter(F.col("before") != F.col("after")).limit(10)

# Transformar para hacer visibles los espacios múltiples
df_vis = (
    df_changed
    .withColumn(
        "before_vis",
        F.regexp_replace("before", r"\s{2,}", "⟶⟶")
    )
)

# Convertir a Pandas
preview_pd = df_vis.select("id", "before_vis", "after").toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: pre;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn("text", F.regexp_replace("text", r"\s{2,}", " "))
df = df.withColumn("text", F.trim(F.col("text")))

# Contar registros con espacios múltiples
count_multi_spaces = df.filter(F.col("text").rlike(r"\s{2,}")).count()

# Crear DataFrame resumen simple
summary = spark.createDataFrame([
    Row(
        Descripcion="Registros con espacios múltiples en el dataframe original",
        Cantidad=count_multi_spaces
    )
])

# Mostrar tabla básica
summary.show(truncate=False)

+---------------------------------------------------------+--------+
|Descripcion                                              |Cantidad|
+---------------------------------------------------------+--------+
|Registros con espacios múltiples en el dataframe original|0       |
+---------------------------------------------------------+--------+



###**Reducción Signos Repetidos**

En este apartado se llevará a cabo la detección de textos que contienen signos de puntuación repetidos de forma exagerada, como múltiples signos de emoción o interrogación consecutivos, los cuales serán removidos y/o corregidos.

Para revisar este comportamiento, primero se mostrará una muestra de registros donde aparezcan estos signos repetidos, permitiendo visualizar el antes y después de la corrección. Luego de verificar que la normalización funciona como se espera, se aplicará la transformación a todo el dataset, reemplazando las secuencias excesivas por un único signo. De esta manera, el texto quedará más equilibrado y uniforme, facilitando su interpretación y su procesamiento en etapas futuras.

In [0]:
# Reducción de signos repetidos
pattern = r"([!?.])\1{2,}"

# Mostrar antes/después
df_preview = (
    df
    .filter(F.col("text").rlike(pattern))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(10)
)

# Reemplazar seguro sin backreferences
df_preview = df_preview.withColumn(
    "after",
    F.regexp_replace("before", r"[!?.]{2,}", F.regexp_extract("before", r"([!?.])\1{2,}", 1))
)

# Convertir a pandas
preview_pd = df_preview.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style='max-height:500px; overflow:auto; font-size:15px;'>
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    F.regexp_replace("text", r"[!?.]{2,}", ".")
)

###**Eliminación URLs**

En este apartado se llevará a cabo la identificación de textos que contienen enlaces o direcciones web, ya que este tipo de elementos no aporta información útil para el análisis lingüístico y puede introducir ruido innecesario en el procesamiento. Para revisar su presencia, se tomará una muestra de registros donde aparezcan URLs y se generará una vista comparativa que mostrará cómo se verá el texto antes y después de eliminarlas.

Una vez confirmado que la limpieza se está aplicando correctamente, la eliminación de URLs se extenderá al resto del conjunto de datos, dejando cada texto libre de enlaces externos. Con ello, se garantizará que el contenido final esté enfocado únicamente en la información textual relevante para las siguientes etapas del pre-procesamiento.

In [0]:
# Detectar registros con URLs
url_pattern = r"(https?://\S+|www\.\S+)"

df_url_preview = (
    df
    .filter(F.col("text").rlike(url_pattern))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(200)
)

# Crear columna after (limpieza)
df_url_preview = df_url_preview.withColumn(
    "after",
    F.regexp_replace("before", url_pattern, "")
)

# Filtrar solo registros donde sí hubo cambios
df_url_changed = df_url_preview.filter(F.col("before") != F.col("after")).limit(10)

# Convertir a Pandas
preview_pd = df_url_changed.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: nowrap;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    F.regexp_replace("text", url_pattern, "")
)

###**Eliminación Correos Electrónicos (Emails)**

En este apartado se llevará a cabo la detección de textos que contienen direcciones de correo electrónico, un tipo de información que no aporta valor al análisis del lenguaje y que podría generar ruido o sesgos innecesarios. Para revisar su presencia, se tomará una muestra de registros donde aparezcan estos patrones y se mostrará una comparación entre el texto original y su versión sin correos electrónicos.

Después de verificar que la limpieza se esté aplicando correctamente, la eliminación de correos electrónicos se realizará sobre todo el conjunto de datos, asegurando que cada texto quede libre de este tipo de información puntual. Con ello, el contenido quedará más enfocado y mejor preparado para las siguientes etapas del proceso de pre-procesamiento.

In [0]:
# Detectar registros con emails
email_pattern = r"[a-zA-Z0-9._%+-]+@[a-zA-Z0-9.-]+\.[a-zA-Z]{2,}"

df_email_preview = (
    df
    .filter(F.col("text").rlike(email_pattern))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(200)
)

# Crear columna after (limpieza)
df_email_preview = df_email_preview.withColumn(
    "after",
    F.regexp_replace("before", email_pattern, "")
)

# Filtrar solo los registros donde sí hubo cambio
df_email_changed = df_email_preview.filter(F.col("before") != F.col("after")).limit(10)

# Convertir a pandas
preview_pd = df_email_changed.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: nowrap;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    F.regexp_replace("text", email_pattern, "")
)

###**Eliminación Menciones (@Usuario)**

En este apartado se identificarán y eliminarán las menciones típicas de redes sociales, es decir, aquellas expresiones que comienzan con @ y hacen referencia a un usuario. Este tipo de elementos no aportará información útil para el análisis y podría interferir con la interpretación del lenguaje.

Primero se generará una muestra para visualizar cómo lucirán los textos antes y después de limpiar estas menciones. Una vez verificado el comportamiento, la transformación se aplicará sobre todo el conjunto de datos, dejando los textos libres de referencias directas a usuarios y conservando únicamente el contenido relevante para las siguientes etapas.

In [0]:
# Detectar registros con menciones
mention_pattern = r"@\w+"

df_mention_preview = (
    df
    .filter(F.col("text").rlike(mention_pattern))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(200)
)

# Crear columna after (limpieza)
df_mention_preview = df_mention_preview.withColumn(
    "after",
    F.regexp_replace("before", mention_pattern, "")
)

# Filtrar solo los registros donde sí hubo cambio
df_mention_changed = df_mention_preview.filter(F.col("before") != F.col("after")).limit(10)

# Convertir a pandas
preview_pd = df_mention_changed.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: nowrap;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    F.regexp_replace("text", mention_pattern, "")
)

###**Eliminación Hashtags (#Palabra)**

En este apartado se detectarán y eliminarán los hashtags, aquellos términos precedidos por el símbolo # que suelen usarse para etiquetar temas. Aunque son útiles para categorizar contenido, no aportarán significado directo al análisis textual y podrán generar ruido innecesario.

Primero se mostrará una vista previa que permitirá comparar cómo luce el texto antes y después de remover los hashtags. Esto ayudará a validar la transformación. Luego, una vez comprobado el resultado, la limpieza se aplicará a todo el conjunto de datos, asegurando que las etiquetas queden fuera y el contenido permanezca centrado en el mensaje real del usuario.

In [0]:
# Detectar registros con hashtags
hashtag_pattern = r"#\w+"

df_hash_preview = (
    df
    .filter(F.col("text").rlike(hashtag_pattern))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(200)
)

# Generar columna after (limpieza)
df_hash_preview = df_hash_preview.withColumn(
    "after",
    F.regexp_replace("before", hashtag_pattern, "")
)

# Filtrar solo los registros donde sí hubo cambio
df_hash_changed = df_hash_preview.filter(F.col("before") != F.col("after")).limit(10)

# Convertir a Pandas
preview_pd = df_hash_changed.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: nowrap;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    F.regexp_replace("text", hashtag_pattern, "")
)

###**Expansión Contracciones & Jerga**

En este apartado se normalizará el lenguaje informal del texto, ampliando tanto contracciones (“don’t”, “i’m”, “can’t”) como expresiones de slang o jerga digital (“idk”, “lol”, “btw”). Este tipo de palabras, pueden dificultar la correcta interpretación del lenguaje por parte de los modelos, ya que acortan o distorsionan conceptos que deberían analizarse en su forma completa.

Para mejorar la claridad del texto, se usará un diccionario que reemplazará estas formas abreviadas por sus equivalentes plenamente expresados. Antes de aplicar el cambio de manera global, se mostrará una vista previa que permitirá comparar cómo se verá el contenido antes y después de la expansión. Con esto se garantizará que el texto gane coherencia y significado, facilitando el procesamiento en etapas posteriores.

In [0]:
# Diccionario contracciones + slang
abb = {
    # Contracciones
    "ain't": "am not",
    "aren't": "are not",
    "can't": "cannot",
    "can't've": "cannot have",
    "'cause": "because",
    "could've": "could have",
    "couldn't": "could not",
    "didn't": "did not",
    "doesn't": "does not",
    "don't": "do not",
    "dont": "do not",
    "hadn't": "had not",
    "hasn't": "has not",
    "haven't": "have not",
    "he's": "he is",
    "i'm": "i am",
    "im": "i am",
    "i've": "i have",
    "isn't": "is not",
    "it's": "it is",
    "let's": "let us",
    "mightn't": "might not",
    "mustn't": "must not",
    "shan't": "shall not",
    "she's": "she is",
    "should've": "should have",
    "shouldn't": "should not",
    "that's": "that is",
    "there's": "there is",
    "they're": "they are",
    "they've": "they have",
    "wasn't": "was not",
    "weren't": "were not",
    "what's": "what is",
    "where's": "where is",
    "who's": "who is",
    "won't": "will not",
    "wouldn't": "would not",
    "you're": "you are",
    "you've": "you have",
    "y'all": "you all",

    # Slang
    "idk": "i do not know",
    "omg": "oh my god",
    "wtf": "what the fuck",
    "wth": "what the hell",
    "lmao": "laughing my ass off",
    "lol": "laughing out loud",
    "btw": "by the way",
    "brb": "be right back",
    "imo": "in my opinion",
    "imho": "in my humble opinion",
    "irl": "in real life",
    "u": "you",
    "ur": "your",
    "thx": "thanks",
    "pls": "please",
    "plz": "please",
    "ppl": "people"
}

# Compilar regex
abb_re = re.compile(r"(?i)\b(" + "|".join(map(re.escape, abb.keys())) + r")\b")

# Función expandir contracciones
def expand_contractions(text):
    if text is None:
        return text

    def replace(match):
        key = match.group(0).lower()
        return abb.get(key, key)

    return abb_re.sub(replace, text)

expand_contractions_udf = F.udf(expand_contractions, StringType())

# Crear preview Antes/Despues
df_preview = (
    df
    .withColumn("before", F.col("text"))
    .withColumn(
        "after",
        expand_contractions_udf(
            F.regexp_replace("before", "’", "'")
        )
    )
    .select("before", "after")
    .orderBy(F.rand())
    .limit(15)
)

# Convertir a pandas
preview_pd = df_preview.toPandas()
html_preview = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_preview}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    expand_contractions_udf(
        F.regexp_replace("text", "’", "'")
    )
)

###**Eliminación Caracteres No Alfabéticos**

En este apartado se eliminarán aquellos símbolos que no forman parte del alfabeto, los números, los espacios o los signos de puntuación básicos. Este tipo de caracteres suele aparecer por errores de codificación, símbolos fuera de contexto, marcas extrañas o elementos que no aportan significado al análisis textual.

Para asegurar que solo se retire contenido realmente innecesario, primero se generará una muestra comparando el texto antes y después de la limpieza. Esto permitirá observar cómo se reducirán estos elementos sin afectar la estructura general del mensaje. Al finalizar, el dataframe quedará compuesto únicamente por caracteres útiles y consistentes para las siguientes secciones del pre-procesamiento.

In [0]:
# Detectar registros con caracteres no alfanuméricos
non_alpha_pattern = r"[^a-zA-Z0-9\s\.\,\!\?\']"

df_nonalpha_preview = (
    df
    .filter(F.col("text").rlike(non_alpha_pattern))
    .orderBy(F.rand())
    .select("id", F.col("text").alias("before"))
    .limit(200)
)

# Crear columna after (limpieza)
df_nonalpha_preview = df_nonalpha_preview.withColumn(
    "after",
    F.regexp_replace("before", non_alpha_pattern, "")
)

# Filtrar solo los registros donde sí hubo cambio
df_nonalpha_changed = df_nonalpha_preview.filter(F.col("before") != F.col("after")).limit(10)

# Convertir a Pandas
preview_pd = df_nonalpha_changed.toPandas()
html_table = preview_pd.to_html(escape=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    white-space: nowrap;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_table}
</div>
"""))

# Aplicar transformación al dataframe original
df = df.withColumn(
    "text",
    F.regexp_replace("text", non_alpha_pattern, "")
)

##**Limpieza Estructural Conjunto Datos**

En esta etapa se llevará a cabo una depuración profunda de la estructura del dataset, garantizando que los registros conserven la coherencia, representatividad y calidad necesarias para continuar con el proceso de modelado. Aquí se identificarán y eliminarán valores atípicos, entradas ruidosas o contenido que no aporte al objetivo analítico, además de revisar la distribución y características generales del texto.

El propósito será asegurar que el conjunto de datos mantenga una base sólida, libre de distorsiones y con una composición adecuada para las etapas posteriores del pre-procesamiento y análisis.

##**Eliminación Outliers Clase Suicide**

En este apartado se llevará a cabo la detección y eliminación de outliers dentro de la clase suicide, con el fin de asegurar que los textos extremadamente cortos o inusualmente largos no afecten la calidad del conjunto de datos. Para ello, se medirá la longitud de cada registro y se identificará qué tan lejos se encuentra del comportamiento típico de esta categoría.

Para mantener la información relevante, se generará una tabla resumen donde se visualizará cuántos casos serán descartados por ser demasiado breves o demasiado extensos. Finalmente, se conservarán únicamente los textos que representen adecuadamente el patrón natural de la clase, integrándolos nuevamente al dataset general y dejándolo listo para continuar con las siguientes etapas del pre-procesamiento.

In [0]:
# Filtrar la clase suicide
df_suicide = df.filter(F.col("class") == "suicide")

# Añadir longitud
df_suicide = df_suicide.withColumn("text_length", F.length("text"))

# Calcular estadísticas Q1, Q3, IQR
stats = df_suicide.select(
    F.percentile_approx("text_length", 0.25).alias("q1"),
    F.percentile_approx("text_length", 0.75).alias("q3")
).collect()[0]

q1 = stats["q1"]
q3 = stats["q3"]
iqr = q3 - q1

py_max = __builtins__.max
lower_bound = py_max(3, q1 - 1.5 * iqr)
upper_bound = int(q3 + 1.5 * iqr)

# Contar outliers
short_outliers = df_suicide.filter(F.col("text_length") < 3).count()
long_outliers  = df_suicide.filter(F.col("text_length") > upper_bound).count()
total_outliers = short_outliers + long_outliers

# Tabla resumen
html_table = f"""
<table border="1" style="border-collapse: collapse; padding: 8px;">
    <tr style="background:#f2f2f2; font-weight:bold;">
        <th>Clase</th>
        <th>Categoría</th>
        <th>Outliers detectados</th>
    </tr>
    <tr>
        <td>suicide</td>
        <td>Textos demasiado cortos (&lt; 3 caracteres)</td>
        <td>{short_outliers}</td>
    </tr>
    <tr>
        <td>suicide</td>
        <td>Textos demasiado largos (&gt; {upper_bound} caracteres)</td>
        <td>{long_outliers}</td>
    </tr>
    <tr style="font-weight:bold;">
        <td>suicide</td>
        <td>Total eliminado</td>
        <td>{total_outliers}</td>
    </tr>
</table>
"""

display(HTML(html_table))

# Eliminar solo outliers de suicide
df_suicide_clean = df_suicide.filter(
    (F.col("text_length") >= 3) &
    (F.col("text_length") <= upper_bound)
).drop("text_length")

# Reintegrar con el dataframe original y mantener clase non-suicide intacta
df = (
    df.filter(F.col("class") != "suicide")
    .unionByName(df_suicide_clean)
)

##**Eliminación Outliers Clase Non-Suicide**

En este apartado se llevará a cabo la detección y eliminación de outliers dentro de la clase non-suicide, con el fin de asegurar que los textos extremadamente cortos o inusualmente largos no afecten la consistencia del conjunto de datos. Para ello, se medirá la longitud de cada registro y se identificará qué tan lejos se encuentra del comportamiento típico de esta categoría.

Para mantener únicamente la información representativa, se generará una tabla resumen donde se visualizará cuántos casos serán descartados por ser demasiado breves o demasiado extensos. Finalmente, se conservarán solo los textos que reflejen adecuadamente el patrón natural de la clase, integrándolos nuevamente al dataset general y dejándolo listo para continuar con las siguientes etapas del pre-procesamiento.

In [0]:
# Filtrar la clase non-suicide
df_non = df.filter(F.col("class") == "non-suicide")

# Añadir longitud
df_non = df_non.withColumn("text_length", F.length("text"))

# Calcular estadísticas Q1, Q3, IQR
stats = df_non.select(
    F.percentile_approx("text_length", 0.25).alias("q1"),
    F.percentile_approx("text_length", 0.75).alias("q3")
).collect()[0]

q1 = stats["q1"]
q3 = stats["q3"]
iqr = q3 - q1

py_max = __builtins__.max
lower_bound = py_max(3, q1 - 1.5 * iqr)
upper_bound = int(q3 + 1.5 * iqr)

# Contar outliers
short_outliers = df_non.filter(F.col("text_length") < 3).count()
long_outliers  = df_non.filter(F.col("text_length") > upper_bound).count()
total_outliers = short_outliers + long_outliers

# Tabla resumen
html_table = f"""
<table border="1" style="border-collapse: collapse; padding: 8px;">
    <tr style="background:#f2f2f2; font-weight:bold;">
        <th>Clase</th>
        <th>Categoría</th>
        <th>Outliers detectados</th>
    </tr>
    <tr>
        <td>non-suicide</td>
        <td>Textos demasiado cortos (&lt; 3 caracteres)</td>
        <td>{short_outliers}</td>
    </tr>
    <tr>
        <td>non-suicide</td>
        <td>Textos demasiado largos (&gt; {upper_bound} caracteres)</td>
        <td>{long_outliers}</td>
    </tr>
    <tr style="font-weight:bold;">
        <td>non-suicide</td>
        <td>Total eliminado</td>
        <td>{total_outliers}</td>
    </tr>
</table>
"""

display(HTML(html_table))

# Eliminar solo outliers de non-suicide
df_non_clean = df_non.filter(
    (F.col("text_length") >= 3) &
    (F.col("text_length") <= upper_bound)
).drop("text_length")

# Reintegrar con el dataframe original y mantener clase suicide intacta
df = (
    df.filter(F.col("class") != "non-suicide")
    .unionByName(df_non_clean)
)

##**Eliminación Ruido Irrelevante (Spam, Publicidad, Etc.)**

En este apartado se llevará a cabo la detección y eliminación de contenido que corresponda a spam, publicidad o mensajes claramente promocionales. Este tipo de registros no aporta información útil para el objetivo del proyecto y, además, puede distorsionar la distribución natural del lenguaje dentro del conjunto de datos.

Para realizar esta depuración, se empleará un conjunto de patrones diseñados para identificar frases comunes de publicidad, llamados a la acción, enlaces externos y expresiones típicas de mensajes automatizados. A partir de esta detección, se generará una vista previa, junto con una tabla que resumirá cuántos registros serán eliminados por pertenecer a esta categoría.

Finalmente, se excluirán por completo los textos marcados como spam, garantizando que el conjunto de datos mantenga únicamente información auténtica y alineada con el propósito del pre-procesamiento.

In [0]:
# Definir patrón de SPAM / publicidad
spam_pattern = r"""(?i)(
    click|clic|haz\s+click|presiona
    |gana\s+dinero|trabaja\s+desde\s+tu\s+casa
    |compra\s+ahora|compra\s+ya|oferta|promoción|descuento
    |suscríbete|subscribe
    |http[s]?:\/\/|www\.
    |llama\s+ya|número\s+gratis
)"""

# Crear columna indicando si es spam
df = df.withColumn("is_spam", F.col("text").rlike(spam_pattern))

# Contar spam detectado
spam_count = df.filter("is_spam = true").count()

# Vista previa antes (top 10)
preview_df = (
    df.filter("is_spam = true")
      .select("id", "text")
      .limit(10)
)

# Después (reemplazo del contenido spam)
preview_df = preview_df.withColumn(
    "text",  
    F.regexp_replace("text", spam_pattern, "")
)

# Convertir a pandas y mostrar tabla HTML
preview_pd = preview_df.toPandas()
html_preview = preview_pd.to_html(escape=False)

display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 650px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
<h3>Vista previa</h3>
{html_preview}
</div>
"""))

# Crear tabla resumen
html_table = f"""
<table border="1" style="border-collapse: collapse; padding: 8px;">
    <tr style="background:#f2f2f2; font-weight:bold;">
        <th>Concepto</th>
        <th>Cantidad</th>
    </tr>
    <tr>
        <td>Registros identificados como SPAM / publicidad</td>
        <td>{spam_count}</td>
    </tr>
    <tr style="font-weight:bold; background:#f9f9f9;">
        <td>Total eliminado</td>
        <td>{spam_count}</td>
    </tr>
</table>
"""

display(HTML(html_table))

# Eliminar spam del dataframe final
df = df.filter("is_spam = false").drop("is_spam")

###**Distribución Longitud Texto Mediante Diagramas De Caja**

En este apartado se generará un boxplot interactivo para observar cómo se distribuyen las longitudes de los textos en cada clase después de la eliminación de outliers. Esta visualización permitirá apreciar la forma general de las distribuciones, su rango típico y las diferencias entre categorías, ofreciendo una perspectiva clara y limpia del comportamiento estructural del dataset.

In [0]:
# Parámetros
max_rows = 232074
seed = 42

# Generar nueva columna con longitud de texto
df_temp = df.withColumn("text_length", length(col("text")))

# Convertir a pandas
pdf = df_temp.select("class", "text_length").toPandas()
pdf["class"] = pdf["class"].astype(str)

# Condicional a max_rows
if len(pdf) > max_rows:
    pdf = pdf.sample(max_rows, random_state=seed)

# Colores pastel ultra suaves
soft_colors = [
    "rgba(102, 194, 165, 0.50)",
    "rgba(141, 160, 203, 0.50)",
    "rgba(252, 141, 98, 0.50)",
    "rgba(231, 138, 195, 0.50)",
    "rgba(166, 216, 84, 0.50)"
]

# Gráfico interactivo
fig = px.box(
    pdf,
    x="class",
    y="text_length",
    points="all",
    hover_data=["text_length", "class"],
    color="class",
    color_discrete_sequence=soft_colors,
    title="Distribución Longitud Texto X Clase - Boxplot"
)

# Ajustes al gráfico interactivo
fig.update_traces(
    pointpos=0,
    jitter=0.30,
    marker=dict(size=3, opacity=0.55, line=dict(width=0)),
    width=0.95
)

# Layout grande y elegante
fig.update_layout(
    title_x=0.5,
    xaxis_title="Clase",
    yaxis_title="Longitud del Texto",
    font=dict(
        family="Algerian, DejaVu Sans, sans-serif",
        size=18
    ),
    template="simple_white",
    height=800,
    width=800,
    showlegend=False,
    margin=dict(l=80, r=80, t=110, b=80)
)

# Zoom basado en IQR global para alargar visualmente las cajas
q1 = pdf['text_length'].quantile(0.25)
q3 = pdf['text_length'].quantile(0.75)
iqr = q3 - q1

# Ajustar el factor para aumentar/disminuir el zoom (1.0 = menos zoom, 2.5 = más zoom)
zoom_factor = 2.5
margin = iqr * zoom_factor

y_min = builtins.max(0, q1 - margin)
y_max = q3 + margin

fig.update_yaxes(range=[y_min, y_max], tickformat=",")

# Mostrar gráfico
fig.show()

%md
###**Distribución Longitud Texto Mediante Diagramas De Violín**

En este apartado se generará un gráfico de violín para analizar la distribución de las longitudes de texto por clase. Esta representación permitirá observar la densidad, variabilidad y forma general de cada categoría después de la limpieza previa, incluyendo outliers eliminados. Además, el gráfico incorporará puntos individuales y una línea de media para ofrecer una visión más completa del comportamiento real de los datos en cada clase.


In [0]:
# Parámetros
max_rows = 232074
seed = 42

# Generar nueva columna con longitud de texto
df_temp = df.withColumn("text_length", length(col("text")))

# Convertir a pandas
pdf = df_temp.select("class", "text_length").toPandas()
pdf["class"] = pdf["class"].astype(str)

# Condicional a máximo registros
if len(pdf) > max_rows:
    pdf = pdf.sample(max_rows, random_state=seed)

# Colores pastel ultra suaves
soft_colors = [
    "rgba(102, 194, 165, 0.50)",
    "rgba(141, 160, 203, 0.50)",
    "rgba(252, 141, 98, 0.50)",
    "rgba(231, 138, 195, 0.50)",
    "rgba(166, 216, 84, 0.50)"
]

# Gráfico de violín
fig = px.violin(
    pdf,
    x="class",
    y="text_length",
    color="class",
    color_discrete_sequence=soft_colors,
    box=True,
    points="all",
    hover_data=["class", "text_length"],
    title="Distribución Longitud Texto X Clase - Violín"
)

# Ajustes estéticos
fig.update_traces(
    meanline_visible=True,
    jitter=0.30,
    marker=dict(
        size=3,
        opacity=0.55,
        line=dict(width=0)
    )
)

# Layout elegante con fuente Algerian
fig.update_layout(
    title_x=0.5,
    xaxis_title="Clase",
    yaxis_title="Longitud del Texto",
    font=dict(
        family="Algerian, DejaVu Sans, sans-serif",
        size=18
    ),
    template="simple_white",
    height=700,
    width=900,
    showlegend=False,
    margin=dict(l=80, r=80, t=110, b=60)
)

fig.update_yaxes(tickformat=",")

# Mostrar gráfico
fig.show()

###**Distribución Clases**

En este apartado se genera un gráfico de barras que muestra la cantidad de textos pertenecientes a cada clase del dataset. Esta visualización permite identificar el nivel de equilibrio o desbalance entre categorías, aportando una vista general del estado final del conjunto de datos después de los procesos de limpieza aplicados.

In [0]:
# Convertir dataframe a pandas
class_dist = df.groupBy("class").count().toPandas().copy()

# Tipos
class_dist["class"] = class_dist["class"].astype(str)
class_dist["count"] = class_dist["count"].astype(int)

# Colores pastel ultra suaves con transparencia
soft_colors = [
    "rgba(102, 194, 165, 0.50)",
    "rgba(141, 160, 203, 0.50)",
    "rgba(252, 141, 98, 0.50)",
    "rgba(231, 138, 195, 0.50)",
    "rgba(166, 216, 84, 0.50)"
]

# Gráfico interactivo
fig = px.bar(
    class_dist,
    x="class",
    y="count",
    text="count",
    color="class",
    color_discrete_sequence=soft_colors,
    hover_data={"count": ":,"}
)

# Ajustar estilo de barras
fig.update_traces(
    width=0.35,
    marker=dict(line=dict(width=0)),
    texttemplate="%{text:,}",
    textposition="outside"
)

# Layout con fuente Algerian
fig.update_layout(
    title="Distribución Clases",
    title_x=0.5,
    xaxis_title="Clase",
    yaxis_title="Cantidad de textos",
    font=dict(
        family="Algerian, DejaVu Sans, sans-serif",
        size=16
    ),
    template="simple_white",
    bargap=0.42,
    showlegend=False,
    height=500,
    width=650,
    margin=dict(l=30, r=30, t=70, b=40)
)

# Números eje Y con separador de miles
fig.update_yaxes(tickformat=",")

fig.show()

###**DataFrame Pre-Procesado Almacenado Unity Catalog**

En este apartado se llevará a cabo la persistencia del conjunto de datos procesado dentro de Unity Catalog, con el fin de garantizar un almacenamiento confiable y versionado mediante el formato Delta. Para ello, se escribirá la tabla resultante sobrescribiendo cualquier versión previa y, posteriormente, se cargará nuevamente desde el catálogo para verificar su correcta creación. Esta operación permitirá disponer de un punto de referencia limpio y centralizado, facilitando consultas posteriores y asegurando continuidad en el flujo de trabajo.

In [0]:
df.write.format("delta").mode("overwrite").saveAsTable(
    "workspace.suicide_detection.suicide_detection_clean"
)

df_clean = spark.table("workspace.suicide_detection.suicide_detection_clean")
display(df_clean)

DataFrame[id: bigint, text: string, class: string]

##**Tokenización & Eliminación Básica**

En esta sección se aplicarán transformaciones iniciales orientadas a descomponer el texto en unidades manejables y depurar elementos que no aportan información útil. El objetivo será obtener representaciones más limpias y consistentes de cada registro, reduciendo ruido lingüístico y preparando la base para etapas posteriores de modelado.

###**Tokenización**

En este apartado se llevará a cabo la tokenización del texto mediante un enfoque basado en expresiones regulares, lo que permitirá descomponer cada mensaje en unidades léxicas limpias y normalizadas. El proceso se enfocará en identificar secuencias válidas de caracteres alfabéticos y descartando fragmentos vacíos o irrelevantes. Para facilitar la inspección del resultado, se generará una vista previa que mostrará cómo los textos originales quedarán representados como listas de tokens depurados, sirviendo como punto de partida para las etapas posteriores del pre-procesamiento.

In [0]:
# Tokenización con RegexTokenizer
tokenizer = RegexTokenizer(
    inputCol="text",
    outputCol="tokens",
    pattern=r"[^a-zA-ZáéíóúñÁÉÍÓÚÑ]+",
    toLowercase=True,
    minTokenLength=1
)

# Crear dataframe df_clean
df_clean = tokenizer.transform(df)

# Eliminar tokens vacíos o nulos
df_clean = df_clean.withColumn(
    "tokens",
    F.expr("filter(tokens, x -> x != '' AND x IS NOT NULL)")
)

# Crear preview
sample_pd = (
    df_clean.select("id", "tokens")
            .limit(10)
            .toPandas()
)

html_preview = sample_pd.to_html(escape=False, index=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 500px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_preview}
</div>
"""))

###**Eliminación Stopwords**

En este apartado se procederá a eliminar las stopwords en inglés con el fin de reducir términos que, aunque frecuentes, no aportan significado relevante al análisis. Para ello, se conservarán los tokens originales en una columna temporal y se aplicará el filtrado utilizando un conjunto estándar de palabras vacías. Posteriormente, se generará una vista comparativa que permitirá observar cómo se depuran las listas de tokens antes y después del proceso. Esta etapa ayudará a concentrar el contenido en unidades realmente informativas, preparando el dataset para fases más avanzadas de procesamiento lingüístico.

In [0]:
# Stopwords en inglés
stopwords_en = StopWordsRemover.loadDefaultStopWords("english")

# Crear columna temporal tokens_before para mostrar antes
df_clean = df_clean.withColumn("tokens_before", F.col("tokens"))

# Configurar y aplicar StopWordsRemover
remover = StopWordsRemover(
    inputCol="tokens",
    outputCol="tokens_after",
    stopWords=stopwords_en
)

df_clean = remover.transform(df_clean)

# Crear preview Antes/Despues
preview = (
    df_clean
    .select("id", "tokens_before", "tokens_after")
    .limit(12)
    .toPandas()
)

html_preview = preview.to_html(escape=False, index=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 550px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    padding: 15px;
    font-size: 15px;
">
{html_preview}
</div>
"""))

# Aplicar transformación al dataframe procesado
df_clean = (
    df_clean
    .drop("tokens")
    .drop("tokens_before")
    .withColumnRenamed("tokens_after", "tokens")
)

###**Eliminación Tokens Cortos/Irrelevantes (1–2 Letras)**

En este apartado se llevará a cabo la eliminación de tokens cortos, con el objetivo de descartar palabras de una o dos letras que no ofrecen valor semántico relevante. Para ello, se conservará temporalmente la versión original de los tokens, lo que permitirá visualizar una comparación directa antes y después del proceso. Una vez aplicado el filtro, se presentará una vista previa de los cambios realizados y, posteriormente, se eliminará la columna auxiliar. Con esta etapa, el conjunto de tokens quedará más depurado y listo para avanzar hacia análisis más precisos y representativos.

In [0]:
# Crear columna temporal con tokens antes del filtrado
df_clean = df_clean.withColumn("tokens_before_shortfilter", F.col("tokens"))

# Aplicar filtro: dejar solo tokens con len >= 3
df_clean = df_clean.withColumn(
    "tokens",
    F.expr("filter(tokens, x -> length(x) >= 3)")
)

# Crear preview Antes/Despues
preview_short = (
    df_clean
    .filter("tokens_before_shortfilter != tokens")
    .select(
        "id",
        F.col("tokens_before_shortfilter").alias("before"),
        F.col("tokens").alias("after")
    )
    .limit(10)
    .toPandas()
)

html_preview_short = preview_short.to_html(escape=False, index=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 600px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    padding: 15px;
">
{html_preview_short}
</div>
"""))

# Eliminar columna temporal
df_clean = df_clean.drop("tokens_before_shortfilter")

##**Procesamiento Lingüístico Profundo**

En esta sección se aplicarán transformaciones lingüísticas profundas orientadas a normalizar y enriquecer el texto, buscando extraer información relevante y representaciones más consistentes de cada registro. El objetivo será reducir ruido semántico y preparar los datos para análisis y modelado más precisos en etapas posteriores.

###**Lematización**

En este apartado se aplicará un proceso de lematización diseñado para reducir cada palabra a una forma más básica y coherente. Para lograrlo, se utilizarán reglas específicas que permiten reconocer variaciones irregulares, eliminar terminaciones innecesarias y unificar palabras que comparten el mismo significado. Antes de transformar los tokens, se conservará una copia temporal para comparar los cambios realizados y visualizar una muestra del resultado. Con este paso, el texto quedará más normalizado y listo para análisis lingüísticos más precisos en fases posteriores.

In [0]:
# Mapeo de formas irregularares
irregulars = {
    # Formas y verbos comunes
    "went":"go","gone":"go","going":"go",
    "was":"be","were":"be","is":"be","are":"be","been":"be","being":"be",
    "has":"have","had":"have","have":"have",
    "does":"do","did":"do","done":"do","doing":"do",
    "saw":"see","seen":"see","seen":"see",
    "took":"take","taken":"take",
    "gave":"give","given":"give",
    "thought":"think","thinking":"think",
    "bought":"buy","brought":"bring",
    "felt":"feel","felt":"feel",
    "found":"find","found":"find",
    "kept":"keep","kept":"keep",
    "left":"leave","left":"leave",
    "lost":"lose","lost":"lose",
    "made":"make","made":"make",
    "met":"meet","met":"meet",
    "paid":"pay","paid":"pay",
    "said":"say","said":"say",
    "sat":"sit","sat":"sit",
    "stood":"stand","stood":"stand",
    "told":"tell","told":"tell",
    "understood":"understand","understood":"understand",
    "won":"win","won":"win",
    "wrote":"write","written":"write",
    "ran":"run","running":"run",
    "ate":"eat","eaten":"eat",
    "drank":"drink","drunk":"drink",
    "sang":"sing","sung":"sing",
    "broke":"break","broken":"break",
    "chose":"choose","chosen":"choose",

    # Formas comunes de auxiliares y modales
    "can":"can","could":"can","may":"may","might":"may","must":"must",
    "shall":"shall","should":"shall","will":"will","would":"will",

    # Adjetivos irregulares / comparativos
    "better":"good","best":"good","worse":"bad","worst":"bad",

    # Algunos sustantivos con formas irregulares
    "children":"child","mice":"mouse","geese":"goose","teeth":"tooth","feet":"foot",
    "men":"man","women":"woman","people":"person","lice":"louse",

    # Participios comunes / formas
    "succeeded":"succeed","failed":"fail","uploaded":"upload","downloaded":"download",
}

# Palabras que NO se deben modificar aunque coincidan con las reglas (lista corta)
safe_exceptions = set([
    "us","as","is","this","that","bus","gas","news","lens","glass","class","boss"
])

# Reemplazos de sufijos con prioridad (primero los más largos)
suffix_rules = [
    # Transformaciones de verbos/sustantivos/adjetivos (sufijo, reemplazo, longitud mínima de la raíz)
    ("ization", "ize", 4),
    ("ational", "ate", 4),
    ("ication", "ic", 4),
    ("tional", "tion", 4),
    ("ational", "ate", 4),
    ("fulness", "ful", 4),
    ("iveness", "ive", 4),
    ("ization", "ize", 4),
    ("ational", "ate", 4),
    ("ization", "ize", 4),
    ("ational", "ate", 4),
    ("isation", "ise", 4),
    ("isation", "ise", 4),
    ("ization", "ize", 4),
    ("ational", "ate", 4),
    ("ication", "ic", 4),
    ("ness", "", 3),
    ("ment", "", 3),
    ("ship", "", 3),
    ("able", "", 4),
    ("ible", "", 4),
    ("ence", "", 4),
    ("ance", "", 4),
    ("ology", "o", 4),
]

# Pequeñas utilidades auxiliares
vowels = set("aeiou")

def has_vowel(s):
    for ch in s:
        if ch in vowels:
            return True
    return False

def safe_candidate(orig, cand):
    """Devuelve True si cand es seguro de usar en lugar de orig"""
    # Debe ser más corto o diferente y tener ≥3 caracteres (a menos que orig sea pequeño)
    if cand == orig:
        return False
    if len(cand) < 3 and len(orig) >= 3:
        return False
    # El candidato debe contener una vocal (para evitar sin sentido)
    if not has_vowel(cand):
        return False
    # Evitar generar tokens sin sentido extremadamente cortos
    if len(cand) < 2:
        return False
    # Evitar modificar las excepciones de la lista blanca
    if orig in safe_exceptions:
        return False
    return True

# Heurísticas para adivinar la categoría gramatical (POS) (muy aproximado) usando tokens del contexto local
def guess_pos(tokens, i):
    """
    Devuelve 'v' (verbo), 'n' (sustantivo), 'adj' (adjetivo), 'adv' (adverbio) o None
    Heurísticas muy simples:
      - si el token anterior es 'to' o un modal/auxiliar → probablemente verbo
      - si termina en 'ly' → adverbio
      - si el sufijo sugiere sustantivo → sustantivo
      - si el token anterior es 'the'/'a' → probablemente sustantivo
    """
    tok = tokens[i].lower() if tokens[i] else tokens[i]
    prev = tokens[i-1].lower() if i-1 >= 0 and tokens[i-1] else None
    if prev in ("to","will","would","should","could","might","may","can","must","did","do","does","did","have","has","had","be","being","been"):
        return "v"
    if tok.endswith("ly"):
        return "adv"
    if tok.endswith("ness") or tok.endswith("ment") or tok.endswith("tion") or tok.endswith("sion") or tok.endswith("ship"):
        return "n"
    if tok.endswith("able") or tok.endswith("ible") or tok.endswith("al") or tok.endswith("ous") or tok.endswith("ive"):
        return "adj"
    if prev in ("the","a","an","this","those","these"):
        return "n"
    return None

# La función principal de lematización
def super_advanced_lemmatize(tokens):
    if tokens is None:
        return []
    out = []
    # Trabajar con la lista de tokens originales para usar heurísticas del contexto local
    for i, t in enumerate(tokens):
        if t is None:
            continue
        orig = t
        w = orig.lower()

        # Mantener URLs/menciones/hashtags/emoticonos tal como están
        if w.startswith("http") or w.startswith("@") or w.startswith("#") or re.search(r"[:;=8][\-~]?[)DPOp/\\]", w):
            out.append(w)
            continue

        # Mantener signos de puntuación o números puros
        if re.fullmatch(r"[\W_]+", w) or re.fullmatch(r"\d+", w):
            out.append(w)
            continue

        # Mantener si el token es corto y común
        if w in safe_exceptions or len(w) <= 2:
            out.append(w)
            continue

        # Búsqueda directa de irregulares
        if w in irregulars:
            out.append(irregulars[w])
            continue

        # Intentar aplicar reglas explícitas de sufijos (orden de prioridad)
        applied = False
        for suf, rep, minroot in suffix_rules:
            if w.endswith(suf) and len(w) - len(suf) >= minroot:
                cand = w[:-len(suf)] + rep
                # Normalizar letras dobles creadas o eliminadas
                if cand.endswith("ie") and not has_vowel(cand[:-2]):
                    pass
                if safe_candidate(w, cand):
                    out.append(cand)
                    applied = True
                    break
        if applied:
            continue

        # Heurística de categoría gramatical (POS)
        pos = guess_pos(tokens, i)

        # Reglas morfológicas según la categoría gramatical estimada
        if pos == "v" or (w.endswith("ing") or w.endswith("ed") or w.endswith("en")):
            # Manejar 'being' → be
            if w == "being":
                out.append("be"); continue

            # -ing
            if w.endswith("ing") and len(w) > 4:
                base = w[:-3]
                # Consonante doble: running → run
                if len(base) > 2 and base[-1] == base[-2]:
                    cand = base[:-1]
                    if safe_candidate(w, cand):
                        out.append(cand); continue
                # Verbos donde la raíz termina en 'e' eliminada: making → make
                if base + "e" not in ("",):
                    cand = base
                    if safe_candidate(w, cand):
                        out.append(cand); continue
                # Recurso/alternativa de respaldo
                if safe_candidate(w, base):
                    out.append(base); continue

            # -ied -> y (studied -> study)
            if w.endswith("ied") and len(w) > 4:
                cand = w[:-3] + "y"
                if safe_candidate(w, cand):
                    out.append(cand); continue

            # -ed
            if w.endswith("ed") and len(w) > 3:
                base = w[:-2]
                if len(base) > 2 and base[-1] == base[-2]:
                    cand = base[:-1]
                    if safe_candidate(w, cand):
                        out.append(cand); continue
                if safe_candidate(w, base):
                    out.append(base); continue

            # -en participio pasado
            if w.endswith("en") and len(w) > 4:
                cand = w[:-2]
                if safe_candidate(w, cand):
                    out.append(cand); continue

        # Manejo tipo sustantivo
        if pos == "n" or (w.endswith("s") or w.endswith("ies") or w.endswith("ves") or w.endswith("es")):
            # 'ies' -> 'y'
            if w.endswith("ies") and len(w) > 4:
                cand = w[:-3] + "y"
                if safe_candidate(w, cand):
                    out.append(cand); continue
            # 'ves' -> 'f'/'fe' elegir 'f'
            if w.endswith("ves") and len(w) > 4:
                cand = w[:-3] + "f"
                if safe_candidate(w, cand):
                    out.append(cand); continue
            # 'es' -> remover
            if w.endswith("es") and len(w) > 3:
                cand = w[:-2]
                if safe_candidate(w, cand):
                    out.append(cand); continue
            # 's' -> singular (evitar ss/us/is)
            if w.endswith("s") and not (w.endswith("ss") or w.endswith("us") or w.endswith("is")) and len(w) > 3:
                cand = w[:-1]
                if safe_candidate(w, cand):
                    out.append(cand); continue

        # Manejo de adjetivos/adverbios
        if pos == "adj" or pos == "adv":
            # -ly -> remover
            if w.endswith("ly") and len(w) > 4:
                cand = w[:-2]
                if safe_candidate(w, cand):
                    out.append(cand); continue
            # -ness -> remover
            if w.endswith("ness") and len(w) > 5:
                cand = w[:-4]
                if safe_candidate(w, cand):
                    out.append(cand); continue
            # Comparativos / superlativos -er/-est
            if w.endswith("er") and len(w) > 4:
                cand = w[:-2]
                if safe_candidate(w, cand):
                    out.append(cand); continue
            if w.endswith("est") and len(w) > 5:
                cand = w[:-3]
                if safe_candidate(w, cand):
                    out.append(cand); continue

        # Verificar manualmente algunos finales comunes
        # Si termina en 'ies' pero el candidato es demasiado corto, volver al original
        if w.endswith("ies") and len(w) <= 4:
            out.append(w); continue

        # Pequeñas heurísticas morfológicas (captura general)
        # Eliminar sufijos simples solo si es seguro
        if w.endswith("ing") and len(w) > 5:
            cand = w[:-3]
            if safe_candidate(w, cand):
                out.append(cand); continue
        if w.endswith("ed") and len(w) > 4:
            cand = w[:-2]
            if safe_candidate(w, cand):
                out.append(cand); continue
        if w.endswith("ly") and len(w) > 4:
            cand = w[:-2]
            if safe_candidate(w, cand):
                out.append(cand); continue

        # Recurso final: mantener el token original en minúsculas
        out.append(w)

    return out

# Registrar UDF para Spark
lemmatize_udf = F.udf(super_advanced_lemmatize, ArrayType(StringType()))

# Columna temporal before
df_clean = df_clean.withColumn("tokens_before_lemma", F.col("tokens"))

# Aplicar lematización
df_clean = df_clean.withColumn("tokens", lemmatize_udf(F.col("tokens")))

# Crear preview Antes/Después
preview_lemma = (
    df_clean
    .filter("tokens_before_lemma != tokens")
    .select(
        "id",
        F.col("tokens_before_lemma").alias("before"),
        F.col("tokens").alias("after")
    )
    .limit(10)
    .toPandas()
)

# Mostrar tabla con scroll
html_preview_lemma = preview_lemma.to_html(escape=False, index=False)

display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 600px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    padding: 15px;
">
{html_preview_lemma}
</div>
"""))

# Eliminar columna temporal
df_clean = df_clean.drop("tokens_before_lemma")

###**Extracción Entidades (NER)**

En este apartado se realizará la extracción automática de entidades relevantes dentro del texto, un proceso conocido como Named Entity Recognition (NER). Para ello se definirán listas de palabras y patrones capaces de detectar menciones sobre medicamentos, sustancias, métodos autolesivos, lugares, personas cercanas, cantidades y expresiones que indiquen riesgo o intención. La función creada analizará cada mensaje y marcará cualquier término asociado a estos grupos, permitiendo identificar señales importantes dentro del contenido. Finalmente, se agregarán columnas con el conteo de entidades encontradas y se generará una vista preliminar para revisar los resultados de manera rápida.

In [0]:
# Listas NER (Named Entity Recognition)

# Medicamentos
medications = [
    "acetaminophen","paracetamol","ibuprofen","aspirin","naproxen",
    "amoxicillin","azithromycin","penicillin","metformin","insulin",
    "atorvastatin","simvastatin","lisinopril","amlodipine","omeprazole",
    "pantoprazole","prednisone","hydrocortisone","albuterol","salbutamol",
    "levothyroxine","warfarin","clopidogrel","gabapentin","pregabalin",
    "tramadol","oxycodone","oxycotin","oxycodone","hydrocodone","vicodin",
    "morphine","fentanyl","codeine","buprenorphine","methadone",
    "diazepam","alprazolam","lorazepam","clonazepam","temazepam",
    "zolpidem","eszopiclone","sertraline","fluoxetine","paroxetine",
    "citalopram","escitalopram","venlafaxine","duloxetine","bupropion",
    "amitriptyline","nortriptyline","imipramine","quetiapine","olanzapine",
    "risperidone","aripiprazole","haloperidol","clozapine","metformin",
    "insulin glargine","insulin lispro","sitagliptin","glipizide",
    "pioglitazone","levetiracetam","valproate","carbamazepine","phenytoin",
    "montelukast","furosemide","hydrochlorothiazide","spironolactone",
    "amlodipine","losartan","valsartan","atenolol","propranolol",
    "digoxin","isotretinoin","tamoxifen","letrozole","trastuzumab",
    "prednisone","methotrexate","cyclophosphamide","infliximab",
    "adalimumab","etanercept","rituximab","ondansetron","promethazine",
    "benzodiazepine","benzo","ssri","snri","tca","mirtazapine",
    "xanax","prozac","zoloft","lexapro","celexa","cymbalta","effexor",
    "valium","ativan","klonopin","ambien","lunesta","seroquel","abilify",
    "vyvanse","adderall","ritalin","concerta","xanac","xanex","prozack"
]

# Sustancias
substances = [
    # recreativo / común
    "alcohol","ethanol","weed","marijuana","cannabis","coke","cocaine",
    "crack","heroin","opiates","opiates","opiate","meth","methamphetamine",
    "mdma","ecstasy","lsd","ketamine","pcp","synthetic cannabinoid",
    "nicotine","tobacco","vape","cigarette","smoke",

    # términos comunes para pastillas/contenedores
    "pill","pills","tablet","tablets","capsule","capsules","dose","doses",
    "bottle","bottles","packet","blister",

    # productos químicos domésticos/peligrosos
    "bleach","detergent","pesticide","insecticide","rodenticide","cyanide",
    "mercury","lead","arsenic","ammonia","chlorine","benzene","toluene",
    "paint thinner","solvent","gasoline","kerosene","antifreeze","ethylene glycol",

    # opioides / sintéticos
    "fentanyl","carfentanil","tramadol","oxycodone","hydrocodone","morphine",
    "codeine","heroin","opium",

    # fármacos comunes repetidos para detección de sustancias
    "acetaminophen","paracetamol","ibuprofen","aspirin","naproxen",

    # patrones regex para formas de nombres químicos
    r"\b[A-Za-z0-9\-]+ine\b",         # ej., chlorine, benzocaine, codeine
    r"\b[A-Za-z0-9\-]+ane\b",         # ej., propane, butane, methane
    r"\b[A-Za-z0-9\-]+ol\b",          # ej., ethanol, methanol
    r"\b[A-Za-z0-9\-]+one\b",         # ej., acetone
    r"\b[A-Za-z0-9\-]+ide\b",         # ej., cyanide, chloride
]

# Metodos suicidas
methods = [
    # sobredosis / envenenamiento
    "overdose","overdosed","take overdose","od","poison","poisoning","ingest poison",
    # corte / instrumento punzante
    "cut","cutting","cut myself","slit","slitting","slash","stab","stabbing",
    # ahorcamiento / asfixia
    "hang","hanging","hang myself","strangle","strangling","asphyxiate",
    # armas de fuego
    "shoot","shoot myself","gun","firearm","shot","shooting",
    # saltos / alturas
    "jump","jumped","jumping","jump off","jump from","jumped off","throw myself",
    # ahogamiento
    "drown","drowning","drown myself",
    # monóxido de carbono
    "carbon monoxide","gas leak","gas oven","car exhaust",
    # vehículo / autopista
    "drive into","run over","pit maneuver","steer into",
    # sofocación / bolsa de plástico
    "suffocate","suffocating","smother","plastic bag","bag over head",
    # fuerza contundente / saltar frente a un tren
    "train","railroad","tracks","jump in front of","bus","truck","fast moving",
    # otros
    "end my life","kill myself","take my life","suicide","self harm","self-harm",
    "self harm attempt","selfharm","attempted suicide"
]

# Ubicación
location = [
    # natural
    "mountain","hill","cliff","ridge","valley","canyon","beach","coast","shore","lake",
    "river","stream","waterfall","sea","ocean","island","forest","wood","desert",
    # urbano / construido por el hombre
    "bridge","tunnel","overpass","underpass","highway","freeway","motorway",
    "road","street","avenue","boulevard","lane","drive","alley","parkway","roundabout",
    "intersection","crosswalk","plaza","square","park","playground","parking lot",
    "parking garage","rooftop","roof","balcony","terrace","stadium","arena",
    "station","train station","bus station","terminal","airport","pier","dock",
    "harbor","pier","wharf","dockside","bridge",
    # instituciones / edificios
    "hospital","clinic","emergency room","er","pharmacy","school","college","university",
    "library","museum","hotel","motel","hostel","casino","church","temple","synagogue",
    "police station","courthouse","court","prison","jail","factory","warehouse",
    # transporte
    "railway","railroad","tracks","subway","metro","tram","light rail",
    "highway ramp","cliff edge","waterfront","pier","dock",
    # regex para direcciones / nombres de calles
    r"\b\d{1,5}\s+[A-Z][a-z0-9\-\. ]{2,50}\b",
    r"\b[A-Z][a-z]+ (Street|St|Avenue|Ave|Road|Rd|Boulevard|Blvd|Lane|Ln|Drive|Dr|Court|Ct)\b"
]

# Personas Familiares
person_family = [
    "mom","mother","mommy","mama","mum","dad","father","daddy","pa","pop",
    "son","daughter","sister","brother","uncle","aunt","grandma","grandfather",
    "grandmother","granddad","grandpa","wife","husband","girlfriend","boyfriend",
    "partner","ex","ex-wife","ex-husband","stepfather","stepmother","stepson",
    "stepdaughter","stepbrother","stepsister","cousin","friend","roommate",
    "neighbor","colleague","boss","manager","therapist","doctor","psychiatrist",
    "nurse","teacher","professor"
]

# Palabras de riesgo de acción
action_risk_words = [
    "think about","thinking about","thought about","plan to","planning to","intend to",
    "intend","intend to kill myself","want to die","want to end my life","want to die",
    "considered suicide","considered","attempt","attempted","tried to","tried",
    "bought pills","bought a gun","got pills","took","took pills","took overdose",
    "overdosed","i want to die","i want to kill myself","i might kill myself",
    "i might end it","ready to die","i cant go on","i can't go on","end it all",
    "end it","suicidal","suicidal thoughts","suicide ideation","kill myself",
    "hurt myself","cut myself","self harm","self-harm","selfharm","i tried",
    "i attempted","going to kill myself","planning to kill myself","i will kill myself"
]

# Patrón de ubicación
location_patterns = [
    # puente con identificador opcional
    r"\bbridge(?:\s+\d{1,4})?\b",
    r"\b(?:railroad|railway|train) (?:tracks|track)\b",
    r"\b(?:parking lot|parking garage|car park)\b",
    r"\brooftop\b",
    r"\bbalcony\b",
    r"\bcliff\b",
    r"\b(seaside|waterfront|pier|dock)\b",
    r"\bhighway\b",
    r"\bfreeway\b",
    r"\bstreet\b",
    r"\b(?:bus|train|subway|metro|tram) station\b",
    r"\bhospital\b",
    r"\ber\b",
    r"\bhome\b",
    r"\bhouse\b",
]

# Mapeo de palabras a números
word_nums = {
    "one":"1","two":"2","three":"3","four":"4","five":"5","six":"6","seven":"7",
    "eight":"8","nine":"9","ten":"10","eleven":"11","twelve":"12","dozen":"12",
    "twenty":"20","thirty":"30"
}

# Busca todas las coincidencias de un patrón regex en un texto
def find_regex_phrases(text, pattern):
    return [m.group(0).strip() for m in re.finditer(pattern, text, flags=re.IGNORECASE)]

# Normaliza una lista: minúsculas, trim, y sin duplicados
def norm_list_unique(lst):
    seen = set()
    out = []
    for x in lst:
        try:
            xn = str(x).strip().lower()
        except:
            xn = ""
        if xn and xn not in seen:
            seen.add(xn)
            out.append(xn)
    return out

# Función principal de extracción (usa text + tokens)
def extract_entities_from(text, tokens):
    """
    Devuelve un diccionario con listas: Person, Location, Medication, Substance, MethodSuicide, Quantity, ActionRisk
    """
    entities = {
        "Person": [],
        "Location": [],
        "Medication": [],
        "Substance": [],
        "MethodSuicide": [],
        "Quantity": [],
        "ActionRisk": []
    }
    if (text is None or str(text).strip() == "") and (tokens is None or len(tokens)==0):
        return entities

    txt = (text or "").strip()
    txt_low = txt.lower()
    toks = [t.lower() for t in (tokens or []) if t is not None]

    # Medications: coincidencia de token O subcadena en el texto (límites de palabra)
    for med in medications:
        if (med in toks) or re.search(r"\b" + re.escape(med.lower()) + r"\b", txt_low):
            entities["Medication"].append(med)

    #Substances: coincidencia de token O patrones regex
    for sub in substances:
        if isinstance(sub, str):
            if (sub in toks) or re.search(r"\b" + re.escape(sub.lower()) + r"\b", txt_low):
                entities["Substance"].append(sub)
        else:
            try:
                if re.search(sub, txt, flags=re.IGNORECASE):
                    entities["Substances"].append(re.search(sub, txt, flags=re.IGNORECASE).group(0))
            except:
                pass

    # Methods: coincidir frases o tokens
    for m in methods:
        if (m in toks) or re.search(r"\b" + re.escape(m.lower()) + r"\b", txt_low):
            entities["MethodSuicide"].append(m)

    # Locations: patrones + heurísticas de tokens
    for pat in location_patterns:
        matches = find_regex_phrases(txt, pat)
        for mm in matches:
            entities["Location"].append(mm)

    # Intentar palabras de ubicación directas de la lista Location
    for loc in location:
        if isinstance(loc, str):
            if (loc.lower() in toks) or re.search(r"\b" + re.escape(loc.lower()) + r"\b", txt_low):
                entities["Location"].append(loc)
        else:
            try:
                m = re.search(loc, txt, flags=re.IGNORECASE)
                if m:
                    entities["LOCATION"].append(m.group(0))
            except:
                pass

    # Person: patrones de menciones familiares y algunas heurísticas de título/nombre
    for fam in person_family:
        if re.search(r"\b(my|the|a|his|her)\s+" + re.escape(fam.lower()) + r"\b", txt_low):
            entities["Person"].append(fam)

    # Título + Apellido / Nombre Apellido (heurística simple sobre el texto original)
    for m in re.finditer(r"\b(?:Dr|Dr\.|Mr|Mr\.|Mrs|Mrs\.|Ms|Ms\.)\s+[A-Z][a-z]{1,}\b", text or ""):
        entities["Person"].append(m.group(0))
    for m in re.finditer(r"\b[A-Z][a-z]{2,}\s+[A-Z][a-z]{2,}\b", text or ""):
        entities["Person"].append(m.group(0))

    # Quantity: dígitos y números escritos en palabras
    for num in re.finditer(r"\b(\d+)\b", txt_low):
        entities["Quantity"].append(num.group(1))
    for w in toks:
        if w in word_nums:
            entities["Quantity"].append(word_nums[w])

    # ActionRisk: frases/verbos que indican planificación o acción
    for ar in action_risk_words:
        if ar in txt_low or ar in toks:
            entities["ActionRisk"].append(ar)

    # Post-procesamiento: normalizar, eliminar duplicados, pasar a minúsculas, mantener un orden razonable
    for k in list(entities.keys()):
        entities[k] = norm_list_unique([str(x) for x in entities[k] if x is not None])

    return entities

# Register UDF en Spark
extract_udf = F.udf(lambda text, tokens: extract_entities_from(text, tokens),
                    MapType(StringType(), ArrayType(StringType())))

# Aplicar y crear la columna entities
df_entities = df_clean.withColumn("entities", extract_udf(F.col("text"), F.col("tokens")))

# Crear columnas numéricas derivadas (counts)
df_entities = (
    df_entities
    .withColumn("ent_person_ct", F.size(F.col("entities").getItem("Person")))
    .withColumn("ent_location_ct", F.size(F.col("entities").getItem("Location")))
    .withColumn("ent_med_ct", F.size(F.col("entities").getItem("Medication")))
    .withColumn("ent_substance_ct", F.size(F.col("entities").getItem("Substance")))
    .withColumn("ent_method_ct", F.size(F.col("entities").getItem("MethodSuicide")))
    .withColumn("ent_qty_ct", F.size(F.col("entities").getItem("Quantity")))
    .withColumn("ent_actionrisk_ct", F.size(F.col("entities").getItem("ActionRisk")))
)

# Aplicar transformación al dataframe original
df_clean = df_entities

# Crear preview de registros
preview_full = (
    df_clean
    .limit(100)
    .toPandas()
)

html_preview_full = preview_full.to_html(escape=False, index=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 700px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    border-radius: 8px;
    padding: 15px;
    box-shadow: 0px 2px 8px rgba(0,0,0,0.15);
    font-size: 14px;
">
{html_preview_full}
</div>
"""))

##**Preparación Final**

En esta sección se realizarán las transformaciones finales necesarias para que los datos puedan ser utilizados por los modelos de aprendizaje automático. Se convertirán los tokens en secuencias numéricas, se aplicará padding para unificar longitudes y se codificarán las etiquetas en un formato compatible con el entrenamiento. Con estos pasos se dejarán las entradas completamente estructuradas y listas para la fase de modelado.

###**Conversión Tokens Secuencias Numéricas**

En este apartado se construirán las representaciones numéricas que utilizará el modelo durante el entrenamiento. Para ello se transformarán los tokens en secuencias de números mediante un tokenizer, se integrarán estas secuencias con las demás características extraídas y se organizará un dataframe final con todos los atributos necesarios. Al finalizar, se generará una vista preliminar que permitirá revisar cómo quedan estructurados los datos antes de pasar a la fase de modelado.

In [0]:
from tensorflow.keras.preprocessing.text import Tokenizer

# Copiar dataframe df_clean 
df_temp = df_clean.withColumn(
    "tokens_str",
    F.concat_ws(" ", F.col("tokens"))
)

# Convertir tokens_str a pandas
df_pd = df_temp.select("tokens_str").toPandas()
tokens_list = df_pd["tokens_str"].tolist()

# Crear y entrenar tokenizer
vocab_size = 20000
tokenizer = Tokenizer(num_words=vocab_size, oov_token="<OOV>")
tokenizer.fit_on_texts(tokens_list)

# Convertir a secuencias numéricas
df_pd["text_token_numeric"] = tokenizer.texts_to_sequences(df_pd["tokens_str"])

# Preparar dataframe final
columns_final = [
    "ent_person_ct", "ent_location_ct", "ent_med_ct",
    "ent_substance_ct", "ent_method_ct",
    "ent_qty_ct", "ent_actionrisk_ct",
    "class"
]

# Extraer las columnas a pandas
df_base = df_temp.select(columns_final).toPandas()

# Insertar text_token_numeric como primera columna
df_base.insert(0, "text_token_numeric", df_pd["text_token_numeric"])

# Convertir a Spark DataFrame final
spark = SparkSession.builder.getOrCreate()
df_features = spark.createDataFrame(df_base)

# Crear preview de registros
preview = df_features.limit(10).toPandas()
html_preview = preview.to_html(escape=False, index=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 400px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    border-radius: 6px;
    padding: 10px;
">
{html_preview}
</div>
"""))

###**Padding Tokens Secuencias Numéricas**

En este apartado se estandarizarán las longitudes de todas las secuencias numéricas generadas previamente. Para ello, se calculará la longitud máxima presente en el conjunto y se aplicará padding en modo post, garantizando que cada registro posea una secuencia uniforme y apta para su ingreso a modelos neuronales. Luego, estas secuencias normalizadas se integrarán nuevamente con el resto de características del dataframe, generando una estructura final coherente y lista para la etapa de entrenamiento.

In [0]:
# Extraer solo la columna de secuencias a pandas
df_seq_pd = df_features.select("text_token_numeric").toPandas()
sequences = df_seq_pd["text_token_numeric"].tolist()

# Obtener la máxima longitud observada en la columna text_token_numeric
max_len = builtins.max(len(seq) for seq in sequences) if len(sequences) > 0 else 0
print("Longitud Máxima = ", max_len)

# Aplicar padding (post)
padded = pad_sequences(
    sequences,
    maxlen=max_len,
    padding="post",
    truncating="post"
)

# Guardar padded (listas) en el dataframe pandas auxiliar
df_seq_pd["text_token_numeric"] = padded.tolist()

# Traer el resto de columnas a pandas
other_cols = [c for c in df_features.columns if c != "text_token_numeric"]
df_other_pd = df_features.select(other_cols).toPandas()

# Insertar la columna padded como primera columna con el nombre original
df_other_pd.insert(0, "text_token_numeric", df_seq_pd["text_token_numeric"])

# Convertir de vuelta a Spark (reemplazando el DataFrame)
spark = SparkSession.builder.getOrCreate()
df_features = spark.createDataFrame(df_other_pd)

# Crear preview de registros
preview = df_features.limit(10).toPandas()
html_preview = preview.to_html(escape=False, index=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 500px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    border-radius: 8px;
    padding: 12px;
    box-shadow: 0px 2px 8px rgba(0,0,0,0.08);
    font-size: 13px;
">
{html_preview}
</div>
"""))

Longitud Máxima =  288


###**Codificación Etiquetas Clase Suicida (Encoding)**

En este apartado se transformarán las etiquetas de la clase suicida del dataset en valores numéricos adecuados para el entrenamiento del modelo. Se asignará 1 a los casos clasificados como suicide y 0 a aquellos marcados como non-suicide, dejando como nulos los valores no reconocidos o inconsistentes. Con esta codificación, el dataframe quedará estandarizado y listo para integrarse en el pipeline de modelado supervisado.

In [0]:
# Reemplazar: non-suicide -> 0, suicide -> 1; valores no reconocidos -> NULL
df_features = df_features.withColumn(
    "class",
    F.when(F.trim(F.lower(F.col("class"))) == "suicide", F.lit(1))
     .when(F.trim(F.lower(F.col("class"))) == "non-suicide", F.lit(0))
     .otherwise(F.lit(None))
     .cast(IntegerType())
)

# Crear preview de registros
preview = df_features.limit(10).toPandas()
html_preview = preview.to_html(escape=False, index=False)

# Mostrar tabla con scroll
display(HTML(f"""
<div style="
    max-width: 100%;
    max-height: 500px;
    overflow-x: auto;
    overflow-y: auto;
    border: 1px solid #ccc;
    border-radius: 8px;
    padding: 12px;
    box-shadow: 0px 2px 8px rgba(0,0,0,0.08);
    font-size: 13px;
">
{html_preview}
</div>
"""))

###**DataFrame Final Procesado Almacenado Unity Catalog**

En este último paso de la etapa de pre-procesamiento se almacenarán las características finales en una tabla Delta dentro del Unity Catalog. Esto permitirá preservar el conjunto de datos limpio, tokenizado, vectorizado y completamente estructurado para su uso en fases posteriores de entrenamiento, validación y experimentación. Al cargar nuevamente la tabla, se verificará que los registros estén disponibles y correctamente formateados.

In [0]:
df_features.write.format("delta").mode("overwrite").saveAsTable(
    "workspace.suicide_detection.suicide_detection_features"
)

df_features = spark.table("workspace.suicide_detection.suicide_detection_features")
display(df_features)

DataFrame[text_token_numeric: array<bigint>, ent_person_ct: int, ent_location_ct: int, ent_med_ct: int, ent_substance_ct: int, ent_method_ct: int, ent_qty_ct: int, ent_actionrisk_ct: int, class: int]